<a href="https://colab.research.google.com/github/bennent/largitdata/blob/master/Bert.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
pip install transformers

In [ ]:
%%bash
#pip install transformers tqdm boto3 requests regex -q

In [ ]:
import torch
from transformers import BertTokenizer
from IPython.display import clear_output

PRETRAINED_MODEL_NAME = "bert-base-chinese"  # 指定繁簡中文 BERT-BASE 預訓練模型

# 取得此預訓練模型所使用的 tokenizer
tokenizer = BertTokenizer.from_pretrained(PRETRAINED_MODEL_NAME)

clear_output()
print("PyTorch 版本：", torch.__version__)

PyTorch 版本： 1.10.0+cu111


In [ ]:
vocab = tokenizer.vocab
print("字典大小：", len(vocab))

字典大小： 21128


In [ ]:
import random
random_tokens = random.sample(list(vocab), 10)
random_ids = [vocab[t] for t in random_tokens]

print("{0:20}{1:15}".format("token", "index"))
print("-" * 25)
for t, id in zip(random_tokens, random_ids):
    print("{0:15}{1:10}".format(t, id))

token               index          
-------------------------
##逝                 19917
##敵                 16204
##氐                 16752
001                  9263
##缘                 18414
loft                12751
##～17               12405
„                     338
mon                  8556
波                    3797


In [ ]:
indices = list(range(647, 657))
some_pairs = [(t, idx) for t, idx in vocab.items() if idx in indices]
for pair in some_pairs:
    print(pair)

('ㄅ', 647)
('ㄆ', 648)
('ㄇ', 649)
('ㄉ', 650)
('ㄋ', 651)
('ㄌ', 652)
('ㄍ', 653)
('ㄎ', 654)
('ㄏ', 655)
('ㄒ', 656)


In [ ]:
text = "[CLS] 等到潮水 [MASK] 了，就知道誰沒穿褲子。"
tokens = tokenizer.tokenize(text)
ids = tokenizer.convert_tokens_to_ids(tokens)

print(text)
print(tokens[:10], '...')
print(ids[:10], '...')

[CLS] 等到潮水 [MASK] 了，就知道誰沒穿褲子。
['[CLS]', '等', '到', '潮', '水', '[MASK]', '了', '，', '就', '知'] ...
[101, 5023, 1168, 4060, 3717, 103, 749, 8024, 2218, 4761] ...


In [ ]:
"""
這段程式碼載入已經訓練好的 masked 語言模型並對有 [MASK] 的句子做預測
"""
from transformers import BertForMaskedLM

# 除了 tokens 以外我們還需要辨別句子的 segment ids
tokens_tensor = torch.tensor([ids])  # (1, seq_len)
segments_tensors = torch.zeros_like(tokens_tensor)  # (1, seq_len)
maskedLM_model = BertForMaskedLM.from_pretrained(PRETRAINED_MODEL_NAME)
clear_output()

# 使用 masked LM 估計 [MASK] 位置所代表的實際 token 
maskedLM_model.eval()
with torch.no_grad():
    outputs = maskedLM_model(tokens_tensor, segments_tensors)
    predictions = outputs[0]
    # (1, seq_len, num_hidden_units)
del maskedLM_model

# 將 [MASK] 位置的機率分佈取 top k 最有可能的 tokens 出來
masked_index = 5
k = 3
probs, indices = torch.topk(torch.softmax(predictions[0, masked_index], -1), k)
predicted_tokens = tokenizer.convert_ids_to_tokens(indices.tolist())

# 顯示 top k 可能的字。一般我們就是取 top 1 當作預測值
print("輸入 tokens ：", tokens[:10], '...')
print('-' * 50)
for i, (t, p) in enumerate(zip(predicted_tokens, probs), 1):
    tokens[masked_index] = t
    print("Top {} ({:2}%)：{}".format(i, int(p.item() * 100), tokens[:10]), '...')

輸入 tokens ： ['[CLS]', '等', '到', '潮', '水', '[MASK]', '了', '，', '就', '知'] ...
--------------------------------------------------
Top 1 (67%)：['[CLS]', '等', '到', '潮', '水', '來', '了', '，', '就', '知'] ...
Top 2 (25%)：['[CLS]', '等', '到', '潮', '水', '濕', '了', '，', '就', '知'] ...
Top 3 ( 2%)：['[CLS]', '等', '到', '潮', '水', '過', '了', '，', '就', '知'] ...


In [ ]:
# 安裝 BertViz
import sys
!test -d bertviz_repo || git clone https://github.com/jessevig/bertviz bertviz_repo
if not 'bertviz_repo' in sys.path:
  sys.path += ['bertviz_repo']

# import packages
from transformers import BertTokenizer, BertModel
from bertviz import head_view

# 在 jupyter notebook 裡頭顯示 visualzation 的 helper
def call_html():
  import IPython
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              "d3": "https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.8/d3.min",
              jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
            },
          });
        </script>
        '''))

clear_output()

In [ ]:
# 記得我們是使用中文 BERT
model_version = 'bert-base-chinese'
model = BertModel.from_pretrained(model_version, output_attentions=True)
tokenizer = BertTokenizer.from_pretrained(model_version)

# 情境 1 的句子
sentence_a = "胖虎叫大雄去買漫畫，"
sentence_b = "回來慢了就打他。"

# 得到 tokens 後丟入 BERT 取得 attention
inputs = tokenizer.encode_plus(sentence_a, sentence_b, return_tensors='pt', add_special_tokens=True)
token_type_ids = inputs['token_type_ids']
input_ids = inputs['input_ids']
attention = model(input_ids, token_type_ids=token_type_ids)[-1]
input_id_list = input_ids[0].tolist() # Batch index 0
tokens = tokenizer.convert_ids_to_tokens(input_id_list)
call_html()

# 交給 BertViz 視覺化
head_view(attention, tokens)

# 注意：執行這段程式碼以後只會顯示下圖左側的結果。
# 為了方便你比較，我把情境 2 的結果也同時附上

Some weights of the model checkpoint at bert-base-chinese were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


<IPython.core.display.Javascript object>

In [ ]:
import glob
glob.glob("*.csv.zip")

['test.csv.zip', 'train.csv.zip']

In [ ]:
"""
前處理原始的訓練數據集。
你不需了解細節，只需要看註解了解邏輯或是輸出的數據格式即可
"""
import os
import pandas as pd

# 解壓縮從 Kaggle 競賽下載的訓練壓縮檔案
os.system("unzip train.csv.zip")

# 簡單的數據清理，去除空白標題的 examples
df_train = pd.read_csv("train.csv")
empty_title = ((df_train['title2_zh'].isnull()) \
               | (df_train['title1_zh'].isnull()) \
               | (df_train['title2_zh'] == '') \
               | (df_train['title2_zh'] == '0'))
df_train = df_train[~empty_title]

# 剔除過長的樣本以避免 BERT 無法將整個輸入序列放入記憶體不多的 GPU
MAX_LENGTH = 30
df_train = df_train[~(df_train.title1_zh.apply(lambda x : len(x)) > MAX_LENGTH)]
df_train = df_train[~(df_train.title2_zh.apply(lambda x : len(x)) > MAX_LENGTH)]

# 只用 1% 訓練數據看看 BERT 對少量標註數據有多少幫助
SAMPLE_FRAC = 0.01
df_train = df_train.sample(frac=SAMPLE_FRAC, random_state=9527)

# 去除不必要的欄位並重新命名兩標題的欄位名
df_train = df_train.reset_index()
df_train = df_train.loc[:, ['title1_zh', 'title2_zh', 'label']]
df_train.columns = ['text_a', 'text_b', 'label']

# idempotence, 將處理結果另存成 tsv 供 PyTorch 使用
df_train.to_csv("train.tsv", sep="\t", index=False)

print("訓練樣本數：", len(df_train))
df_train.head()

訓練樣本數： 2657


text_a                          text_b      label
0       苏有朋要结婚了，但网友觉得他还是和林心如比较合适  好闺蜜结婚给不婚族的秦岚扔花球，倒霉的秦岚掉水里笑哭苏有朋！  unrelated
1  爆料李小璐要成前妻了贾乃亮模仿王宝强一步到位、快刀斩乱麻！  李小璐要变前妻了？贾乃亮可能效仿王宝强当机立断，快刀斩乱麻！     agreed
2  为彩礼，母亲把女儿嫁给陌生男子，十年后再见面，母亲湿了眼眶  阿姨，不要彩礼是觉得你家穷，给你台阶下，不要以为我嫁不出去！  unrelated
3         猪油是个宝，一勺猪油等于十副药，先备起来再说  传承千百的猪油为何变得人人唯恐避之不及？揭开猪油的四大谣言！  unrelated
4                  剖析：香椿，为什么会致癌？            香椿含亚硝酸盐多吃会致癌？测完发现是谣言  disagreed

In [ ]:
df_train.label.value_counts() / len(df_train)

unrelated    0.679338
agreed       0.294317
disagreed    0.026346
Name: label, dtype: float64

In [ ]:
os.system("unzip test.csv.zip")
df_test = pd.read_csv("test.csv")
df_test = df_test.loc[:, ["title1_zh", "title2_zh", "id"]]
df_test.columns = ["text_a", "text_b", "Id"]
df_test.to_csv("test.tsv", sep="\t", index=False)

print("預測樣本數：", len(df_test))
df_test.head()

預測樣本數： 80126


text_a                       text_b      Id
0  萨拉赫人气爆棚!埃及总统大选未参选获百万选票 现任总统压力山大  辟谣！里昂官方否认费基尔加盟利物浦，难道是价格没谈拢？  321187
1              萨达姆被捕后告诫美国的一句话，发人深思    10大最让美国人相信的荒诞谣言，如蜥蜴人掌控着美国  321190
2    萨达姆此项计划没有此国破坏的话，美国还会对伊拉克发动战争吗          萨达姆被捕后告诫美国的一句话，发人深思  321189
3              萨达姆被捕后告诫美国的一句话，发人深思  被绞刑处死的萨达姆是替身？他的此男人举动击破替身谣言！  321193
4              萨达姆被捕后告诫美国的一句话，发人深思         中国川贝枇杷膏在美国受到热捧？纯属谣言！  321191

In [ ]:
ratio = len(df_test) / len(df_train)
print("測試集樣本數 / 訓練集樣本數 = {:.1f} 倍".format(ratio))


測試集樣本數 / 訓練集樣本數 = 30.2 倍


In [ ]:
"""
實作一個可以用來讀取訓練 / 測試集的 Dataset，這是你需要徹底了解的部分。
此 Dataset 每次將 tsv 裡的一筆成對句子轉換成 BERT 相容的格式，並回傳 3 個 tensors：
- tokens_tensor：兩個句子合併後的索引序列，包含 [CLS] 與 [SEP]
- segments_tensor：可以用來識別兩個句子界限的 binary tensor
- label_tensor：將分類標籤轉換成類別索引的 tensor, 如果是測試集則回傳 None
"""
!pip install pysnooper -q
import pysnooper



from torch.utils.data import Dataset
 
    
class FakeNewsDataset(Dataset):
    # 讀取前處理後的 tsv 檔並初始化一些參數
    def __init__(self, mode, tokenizer):
        assert mode in ["train", "test"]  # 一般訓練你會需要 dev set
        self.mode = mode
        # 大數據你會需要用 iterator=True
        self.df = pd.read_csv(mode + ".tsv", sep="\t").fillna("")
        self.len = len(self.df)
        self.label_map = {'agreed': 0, 'disagreed': 1, 'unrelated': 2}
        self.tokenizer = tokenizer  # 我們將使用 BERT tokenizer
    @pysnooper.snoop()# 加入以瞭解所有轉換過程
    # 定義回傳一筆訓練 / 測試數據的函式
    def __getitem__(self, idx):
        if self.mode == "test":
            text_a, text_b = self.df.iloc[idx, :2].values
            label_tensor = None
        else:
            text_a, text_b, label = self.df.iloc[idx, :].values
            # 將 label 文字也轉換成索引方便轉換成 tensor
            label_id = self.label_map[label]
            label_tensor = torch.tensor(label_id)
            
        # 建立第一個句子的 BERT tokens 並加入分隔符號 [SEP]
        word_pieces = ["[CLS]"]
        tokens_a = self.tokenizer.tokenize(text_a)
        word_pieces += tokens_a + ["[SEP]"]
        len_a = len(word_pieces)
        
        # 第二個句子的 BERT tokens
        tokens_b = self.tokenizer.tokenize(text_b)
        word_pieces += tokens_b + ["[SEP]"]
        len_b = len(word_pieces) - len_a
        
        # 將整個 token 序列轉換成索引序列
        ids = self.tokenizer.convert_tokens_to_ids(word_pieces)
        tokens_tensor = torch.tensor(ids)
        
        # 將第一句包含 [SEP] 的 token 位置設為 0，其他為 1 表示第二句
        segments_tensor = torch.tensor([0] * len_a + [1] * len_b, 
                                        dtype=torch.long)
        
        return (tokens_tensor, segments_tensor, label_tensor)
    
    def __len__(self):
        return self.len
    
    
# 初始化一個專門讀取訓練樣本的 Dataset，使用中文 BERT 斷詞
trainset = FakeNewsDataset("train", tokenizer=tokenizer)

In [ ]:
# 選擇第一個樣本
sample_idx = 0

# 將原始文本拿出做比較
text_a, text_b, label = trainset.df.iloc[sample_idx].values

# 利用剛剛建立的 Dataset 取出轉換後的 id tensors
tokens_tensor, segments_tensor, label_tensor = trainset[sample_idx]

# 將 tokens_tensor 還原成文本
tokens = tokenizer.convert_ids_to_tokens(tokens_tensor.tolist())
combined_text = "".join(tokens)

# 渲染前後差異，毫無反應就是個 print。可以直接看輸出結果
print(f"""[原始文本]
句子 1：{text_a}
句子 2：{text_b}
分類  ：{label}

--------------------

[Dataset 回傳的 tensors]
tokens_tensor  ：{tokens_tensor}

segments_tensor：{segments_tensor}

label_tensor   ：{label_tensor}

--------------------

[還原 tokens_tensors]
{combined_text}
""")


PYDEV DEBUGGER WARNING:
sys.settrace() should not be used when the debugger is being used.
This may cause the debugger to stop working correctly.
If this is needed, please check: 
http://pydev.blogspot.com/2007/06/why-cant-pydev-debugger-work-with.html
to see how to restore the debug tracing back correctly.
Call Location:
  File "/usr/local/lib/python3.7/dist-packages/pysnooper/tracer.py", line 340, in __enter__
    sys.settrace(self.trace)

Source path:... <ipython-input-40-03c31f6405b1>
Starting var:.. self = <__main__.FakeNewsDataset object at 0x7fec0de2ead0>
Starting var:.. idx = 0
04:45:02.932576 call        28     def __getitem__(self, idx):
04:45:02.934892 line        29         if self.mode == "test":
04:45:02.935267 line        33             text_a, text_b, label = self.df.iloc[idx, :].values
New var:....... text_a = '苏有朋要结婚了，但网友觉得他还是和林心如比较合适'
New var:....... text_b = '好闺蜜结婚给不婚族的秦岚扔花球，倒霉的秦岚掉水里笑哭苏有朋！'
New var:....... label = 'unrelated'
04:45:02.938621 line        35         

[原始文本]
句子 1：苏有朋要结婚了，但网友觉得他还是和林心如比较合适
句子 2：好闺蜜结婚给不婚族的秦岚扔花球，倒霉的秦岚掉水里笑哭苏有朋！
分類  ：unrelated

--------------------

[Dataset 回傳的 tensors]
tokens_tensor  ：tensor([ 101, 5722, 3300, 3301, 6206, 5310, 2042,  749, 8024,  852, 5381, 1351,
        6230, 2533,  800, 6820, 3221, 1469, 3360, 2552, 1963, 3683, 6772, 1394,
        6844,  102, 1962, 7318, 6057, 5310, 2042, 5314,  679, 2042, 3184, 4638,
        4912, 2269, 2803, 5709, 4413, 8024,  948, 7450, 4638, 4912, 2269, 2957,
        3717, 7027, 5010, 1526, 5722, 3300, 3301, 8013,  102])

segments_tensor：tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1])

label_tensor   ：2

--------------------

[還原 tokens_tensors]
[CLS]苏有朋要结婚了，但网友觉得他还是和林心如比较合适[SEP]好闺蜜结婚给不婚族的秦岚扔花球，倒霉的秦岚掉水里笑哭苏有朋！[SEP]



Elapsed time: 00:00:00.043779


In [ ]:
"""
實作可以一次回傳一個 mini-batch 的 DataLoader
這個 DataLoader 吃我們上面定義的 `FakeNewsDataset`，
回傳訓練 BERT 時會需要的 4 個 tensors：
- tokens_tensors  : (batch_size, max_seq_len_in_batch)
- segments_tensors: (batch_size, max_seq_len_in_batch)
- masks_tensors   : (batch_size, max_seq_len_in_batch)
- label_ids       : (batch_size)
"""

from torch.utils.data import DataLoader
from torch.nn.utils.rnn import pad_sequence

# 這個函式的輸入 `samples` 是一個 list，裡頭的每個 element 都是
# 剛剛定義的 `FakeNewsDataset` 回傳的一個樣本，每個樣本都包含 3 tensors：
# - tokens_tensor
# - segments_tensor
# - label_tensor
# 它會對前兩個 tensors 作 zero padding，並產生前面說明過的 masks_tensors
def create_mini_batch(samples):
    tokens_tensors = [s[0] for s in samples]
    segments_tensors = [s[1] for s in samples]
    
    # 測試集有 labels
    if samples[0][2] is not None:
        label_ids = torch.stack([s[2] for s in samples])
    else:
        label_ids = None
    
    # zero pad 到同一序列長度
    tokens_tensors = pad_sequence(tokens_tensors, 
                                  batch_first=True)
    segments_tensors = pad_sequence(segments_tensors, 
                                    batch_first=True)
    
    # attention masks，將 tokens_tensors 裡頭不為 zero padding
    # 的位置設為 1 讓 BERT 只關注這些位置的 tokens
    masks_tensors = torch.zeros(tokens_tensors.shape, 
                                dtype=torch.long)
    masks_tensors = masks_tensors.masked_fill(
        tokens_tensors != 0, 1)
    
    return tokens_tensors, segments_tensors, masks_tensors, label_ids


# 初始化一個每次回傳 64 個訓練樣本的 DataLoader
# 利用 `collate_fn` 將 list of samples 合併成一個 mini-batch 是關鍵
BATCH_SIZE = 64
trainloader = DataLoader(trainset, batch_size=BATCH_SIZE, 
                         collate_fn=create_mini_batch)

In [ ]:
data = next(iter(trainloader))

tokens_tensors, segments_tensors, \
    masks_tensors, label_ids = data

print(f"""
tokens_tensors.shape   = {tokens_tensors.shape} 
{tokens_tensors}
------------------------
segments_tensors.shape = {segments_tensors.shape}
{segments_tensors}
------------------------
masks_tensors.shape    = {masks_tensors.shape}
{masks_tensors}
------------------------
label_ids.shape        = {label_ids.shape}
{label_ids}
""")

Starting var:.. self = <__main__.FakeNewsDataset object at 0x7fec0de2ead0>
Starting var:.. idx = 0
04:45:03.056016 call        28     def __getitem__(self, idx):
04:45:03.057643 line        29         if self.mode == "test":
04:45:03.057797 line        33             text_a, text_b, label = self.df.iloc[idx, :].values
New var:....... text_a = '苏有朋要结婚了，但网友觉得他还是和林心如比较合适'
New var:....... text_b = '好闺蜜结婚给不婚族的秦岚扔花球，倒霉的秦岚掉水里笑哭苏有朋！'
New var:....... label = 'unrelated'
04:45:03.058919 line        35             label_id = self.label_map[label]
New var:....... label_id = 2
04:45:03.059158 line        36             label_tensor = torch.tensor(label_id)
New var:....... label_tensor = tensor(2)
04:45:03.059392 line        39         word_pieces = ["[CLS]"]
New var:....... word_pieces = ['[CLS]']
04:45:03.059872 line        40         tokens_a = self.tokenizer.tokenize(text_a)
New var:....... tokens_a = ['苏', '有', '朋', '要', '结', '婚', '了', '，', '但', '网...'还', '是', '和', '林', '心', '如', '比', '较', '合',


tokens_tensors.shape   = torch.Size([64, 63]) 
tensor([[ 101, 5722, 3300,  ...,    0,    0,    0],
        [ 101, 4255, 3160,  ..., 8013,  102,    0],
        [ 101,  711, 2506,  ..., 8013,  102,    0],
        ...,
        [ 101,  671, 2157,  ...,    0,    0,    0],
        [ 101, 1380,  677,  ...,    0,    0,    0],
        [ 101, 2458, 1853,  ...,    0,    0,    0]])
------------------------
segments_tensors.shape = torch.Size([64, 63])
tensor([[0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 1, 1, 0],
        [0, 0, 0,  ..., 1, 1, 0],
        ...,
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0]])
------------------------
masks_tensors.shape    = torch.Size([64, 63])
tensor([[1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 1, 1, 0],
        [1, 1, 1,  ..., 1, 1, 0],
        ...,
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0]])
------------------------
label_ids.shape        

In [ ]:
# 載入一個可以做中文多分類任務的模型，n_class = 3
from transformers import BertForSequenceClassification

PRETRAINED_MODEL_NAME = "bert-base-chinese"
NUM_LABELS = 3

model = BertForSequenceClassification.from_pretrained(
    PRETRAINED_MODEL_NAME, num_labels=NUM_LABELS)

clear_output()

# high-level 顯示此模型裡的 modules
print("""
name            module
----------------------""")
for name, module in model.named_children():
    if name == "bert":
        for n, _ in module.named_children():
            print(f"{name}:{n}")
    else:
        print("{:15} {}".format(name, module))


name            module
----------------------
bert:embeddings
bert:encoder
bert:pooler
dropout         Dropout(p=0.1, inplace=False)
classifier      Linear(in_features=768, out_features=3, bias=True)


In [ ]:
class BertForSequenceClassification():
    def __init__(self, config, num_labels=2):
        super(BertForSequenceClassification, self).__init__(config)
        self.num_labels = num_labels
        self.bert = BertModel(config, ...)  # 載入預訓練 BERT
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        # 簡單 linear 層
        self.classifier = nn.Linear(config.hidden_size, num_labels)

    def forward(self, input_ids, token_type_ids=None, attention_mask=None, labels=None):
        # BERT 輸入就是 tokens, segments, masks
        outputs = self.bert(input_ids, token_type_ids, attention_mask)
        ...
        pooled_output = self.dropout(pooled_output)
        # 線性分類器將 dropout 後的 BERT repr. 轉成類別 logits
        logits = self.classifier(pooled_output)

        # 輸入有 labels 的話直接計算 Cross Entropy 回傳，方便！
        if labels is not None:
            loss_fct = CrossEntropyLoss()
            loss = loss_fct(logits.view(-1, self.num_labels), labels.view(-1))
            return loss
        # 有要求回傳注意矩陣的話回傳
        elif self.output_attentions:
            return all_attentions, logits
        # 回傳各類別的 logits
        return logits

In [ ]:
model.config

BertConfig {
  "_name_or_path": "bert-base-chinese",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "directionality": "bidi",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1",
    "2": "LABEL_2"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1,
    "LABEL_2": 2
  },
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "pooler_fc_size": 768,
  "pooler_num_attention_heads": 12,
  "pooler_num_fc_layers": 3,
  "pooler_size_per_head": 128,
  "pooler_type": "first_token_transform",
  "position_embedding_type": "absolute",
  "transformers_version": "4.16.2",
  "type_vocab_size": 2,
  "use_cache": true,
  "vocab_size": 21128
}

In [ ]:
"""
定義一個可以針對特定 DataLoader 取得模型預測結果以及分類準確度的函式
之後也可以用來生成上傳到 Kaggle 競賽的預測結果

2019/11/22 更新：在將 `tokens`、`segments_tensors` 等 tensors
丟入模型時，強力建議指定每個 tensor 對應的參數名稱，以避免 HuggingFace
更新 repo 程式碼並改變參數順序時影響到我們的結果。
"""

def get_predictions(model, dataloader, compute_acc=False):
    predictions = None
    correct = 0
    total = 0
      
    with torch.no_grad():
        # 遍巡整個資料集
        for data in dataloader:
            # 將所有 tensors 移到 GPU 上
            if next(model.parameters()).is_cuda:
                data = [t.to("cuda:0") for t in data if t is not None]
            
            
            # 別忘記前 3 個 tensors 分別為 tokens, segments 以及 masks
            # 且強烈建議在將這些 tensors 丟入 `model` 時指定對應的參數名稱
            tokens_tensors, segments_tensors, masks_tensors = data[:3]
            outputs = model(input_ids=tokens_tensors, 
                            token_type_ids=segments_tensors, 
                            attention_mask=masks_tensors)
            
            logits = outputs[0]
            _, pred = torch.max(logits.data, 1)
            
            # 用來計算訓練集的分類準確率
            if compute_acc:
                labels = data[3]
                total += labels.size(0)
                correct += (pred == labels).sum().item()
                
            # 將當前 batch 記錄下來
            if predictions is None:
                predictions = pred
            else:
                predictions = torch.cat((predictions, pred))
    
    if compute_acc:
        acc = correct / total
        return predictions, acc
    return predictions
    
# 讓模型跑在 GPU 上並取得訓練集的分類準確率
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print("device:", device)
model = model.to(device)
_, acc = get_predictions(model, trainloader, compute_acc=True)
print("classification acc:", acc)

device: cpu


串流輸出內容已截斷至最後 5000 行。
New var:....... segments_tensor = tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])
04:53:25.944454 line        57         return (tokens_tensor, segments_tensor, label_tensor)
04:53:25.945423 return      57         return (tokens_tensor, segments_tensor, label_tensor)
Return value:.. (tensor([ 101, 2544,  928, 5408,  837, 3064, 212... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]), tensor(2))
Elapsed time: 00:00:00.018024
Starting var:.. self = <__main__.FakeNewsDataset object at 0x7fec0de2ead0>
Starting var:.. idx = 2522
04:53:25.948381 call        28     def __getitem__(self, idx):
04:53:25.948549 line        29         if self.mode == "test":
04:53:25.948636 line        33             text_a, text_b, label = self.df.iloc[idx, :].values
New var:....... text_a = '兴化荻垛发生一偷小孩事件 嫌疑人被群殴后已送警'
New var:....... text_b = '小孩装纸箱丢弃？泉州网警巡查执法官微：谣言'
New var:....... label = 'unrelated'
04:53:25.949377 line        35             label_id 

classification acc: 0.29657508468197213


In [ ]:
def get_learnable_params(module):
    return [p for p in module.parameters() if p.requires_grad]
     
model_params = get_learnable_params(model)
clf_params = get_learnable_params(model.classifier)

print(f"""
整個分類模型的參數量：{sum(p.numel() for p in model_params)}
線性分類器的參數量：{sum(p.numel() for p in clf_params)}
""")


整個分類模型的參數量：102269955
線性分類器的參數量：2307



In [ ]:
%%time

# 訓練模式
model.train()

# 使用 Adam Optim 更新整個分類模型的參數
optimizer = torch.optim.Adam(model.parameters(), lr=1e-5)


EPOCHS = 6  # 幸運數字
for epoch in range(EPOCHS):
    
    running_loss = 0.0
    for data in trainloader:
        
        tokens_tensors, segments_tensors, \
        masks_tensors, labels = [t.to(device) for t in data]

        # 將參數梯度歸零
        optimizer.zero_grad()
        
        # forward pass
        outputs = model(input_ids=tokens_tensors, 
                        token_type_ids=segments_tensors, 
                        attention_mask=masks_tensors, 
                        labels=labels)

        loss = outputs[0]
        # backward
        loss.backward()
        optimizer.step()


        # 紀錄當前 batch loss
        running_loss += loss.item()
        
    # 計算分類準確率
    _, acc = get_predictions(model, trainloader, compute_acc=True)

    print('[epoch %d] loss: %.3f, acc: %.3f' %
          (epoch + 1, running_loss, acc))
    

串流輸出內容已截斷至最後 5000 行。
New var:....... segments_tensor = tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])
05:25:57.625484 line        57         return (tokens_tensor, segments_tensor, label_tensor)
05:25:57.626431 return      57         return (tokens_tensor, segments_tensor, label_tensor)
Return value:.. (tensor([ 101, 2544,  928, 5408,  837, 3064, 212... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]), tensor(2))
Elapsed time: 00:00:00.017807
Starting var:.. self = <__main__.FakeNewsDataset object at 0x7fec0de2ead0>
Starting var:.. idx = 2522
05:25:57.629022 call        28     def __getitem__(self, idx):
05:25:57.629186 line        29         if self.mode == "test":
05:25:57.629285 line        33             text_a, text_b, label = self.df.iloc[idx, :].values
New var:....... text_a = '兴化荻垛发生一偷小孩事件 嫌疑人被群殴后已送警'
New var:....... text_b = '小孩装纸箱丢弃？泉州网警巡查执法官微：谣言'
New var:....... label = 'unrelated'
05:25:57.629995 line        35             label_id 

[epoch 1] loss: 31.821, acc: 0.736


串流輸出內容已截斷至最後 5000 行。
New var:....... segments_tensor = tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])
05:58:27.001839 line        57         return (tokens_tensor, segments_tensor, label_tensor)
05:58:27.003662 return      57         return (tokens_tensor, segments_tensor, label_tensor)
Return value:.. (tensor([ 101, 2544,  928, 5408,  837, 3064, 212... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]), tensor(2))
Elapsed time: 00:00:00.023465
Starting var:.. self = <__main__.FakeNewsDataset object at 0x7fec0de2ead0>
Starting var:.. idx = 2522
05:58:27.012546 call        28     def __getitem__(self, idx):
05:58:27.012719 line        29         if self.mode == "test":
05:58:27.012804 line        33             text_a, text_b, label = self.df.iloc[idx, :].values
New var:....... text_a = '兴化荻垛发生一偷小孩事件 嫌疑人被群殴后已送警'
New var:....... text_b = '小孩装纸箱丢弃？泉州网警巡查执法官微：谣言'
New var:....... label = 'unrelated'
05:58:27.013563 line        35             label_id 

[epoch 2] loss: 19.920, acc: 0.843


串流輸出內容已截斷至最後 5000 行。
New var:....... segments_tensor = tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])
06:30:47.248393 line        57         return (tokens_tensor, segments_tensor, label_tensor)
06:30:47.249292 return      57         return (tokens_tensor, segments_tensor, label_tensor)
Return value:.. (tensor([ 101, 2544,  928, 5408,  837, 3064, 212... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]), tensor(2))
Elapsed time: 00:00:00.011764
Starting var:.. self = <__main__.FakeNewsDataset object at 0x7fec0de2ead0>
Starting var:.. idx = 2522
06:30:47.251312 call        28     def __getitem__(self, idx):
06:30:47.251470 line        29         if self.mode == "test":
06:30:47.251561 line        33             text_a, text_b, label = self.df.iloc[idx, :].values
New var:....... text_a = '兴化荻垛发生一偷小孩事件 嫌疑人被群殴后已送警'
New var:....... text_b = '小孩装纸箱丢弃？泉州网警巡查执法官微：谣言'
New var:....... label = 'unrelated'
06:30:47.252256 line        35             label_id 

...

[epoch 4] loss: 12.077, acc: 0.903


串流輸出內容已截斷至最後 5000 行。
New var:....... segments_tensor = tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])
07:35:54.256404 line        57         return (tokens_tensor, segments_tensor, label_tensor)
07:35:54.257311 return      57         return (tokens_tensor, segments_tensor, label_tensor)
Return value:.. (tensor([ 101, 2544,  928, 5408,  837, 3064, 212... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]), tensor(2))
Elapsed time: 00:00:00.017010
Starting var:.. self = <__main__.FakeNewsDataset object at 0x7fec0de2ead0>
Starting var:.. idx = 2522
07:35:54.260011 call        28     def __getitem__(self, idx):
07:35:54.260228 line        29         if self.mode == "test":
07:35:54.260822 line        33             text_a, text_b, label = self.df.iloc[idx, :].values
New var:....... text_a = '兴化荻垛发生一偷小孩事件 嫌疑人被群殴后已送警'
New var:....... text_b = '小孩装纸箱丢弃？泉州网警巡查执法官微：谣言'
New var:....... label = 'unrelated'
07:35:54.261823 line        35             label_id 

[epoch 5] loss: 9.237, acc: 0.948


串流輸出內容已截斷至最後 5000 行。
New var:....... segments_tensor = tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])
08:08:14.352268 line        57         return (tokens_tensor, segments_tensor, label_tensor)
08:08:14.353441 return      57         return (tokens_tensor, segments_tensor, label_tensor)
Return value:.. (tensor([ 101, 2544,  928, 5408,  837, 3064, 212... 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]), tensor(2))
Elapsed time: 00:00:00.020401
Starting var:.. self = <__main__.FakeNewsDataset object at 0x7fec0de2ead0>
Starting var:.. idx = 2522
08:08:14.356111 call        28     def __getitem__(self, idx):
08:08:14.356294 line        29         if self.mode == "test":
08:08:14.356386 line        33             text_a, text_b, label = self.df.iloc[idx, :].values
New var:....... text_a = '兴化荻垛发生一偷小孩事件 嫌疑人被群殴后已送警'
New var:....... text_b = '小孩装纸箱丢弃？泉州网警巡查执法官微：谣言'
New var:....... label = 'unrelated'
08:08:14.357069 line        35             label_id 

[epoch 6] loss: 7.187, acc: 0.911
CPU times: user 3h 11min 10s, sys: 4min 45s, total: 3h 15min 56s
Wall time: 3h 14min 48s


In [ ]:
%%time
# 建立測試集。這邊我們可以用跟訓練時不同的 batch_size，看你 GPU 多大
testset = FakeNewsDataset("test", tokenizer=tokenizer)
testloader = DataLoader(testset, batch_size=256, 
                        collate_fn=create_mini_batch)

# 用分類模型預測測試集
predictions = get_predictions(model, testloader)

# 用來將預測的 label id 轉回 label 文字
index_map = {v: k for k, v in testset.label_map.items()}

# 生成 Kaggle 繳交檔案
df = pd.DataFrame({"Category": predictions.tolist()})
df['Category'] = df.Category.apply(lambda x: index_map[x])
df_pred = pd.concat([testset.df.loc[:, ["Id"]], 
                          df.loc[:, 'Category']], axis=1)
df_pred.to_csv('bert_1_prec_training_samples.csv', index=False)
df_pred.head()

串流輸出內容已截斷至最後 5000 行。
13:17:18.977874 return      57         return (tokens_tensor, segments_tensor, label_tensor)
Return value:.. (tensor([ 101, 7970, 7970, 1506, 2209, 2356, 330...1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]), None)
Elapsed time: 00:00:00.015971
Starting var:.. self = <__main__.FakeNewsDataset object at 0x7feb06264550>
Starting var:.. idx = 79979
13:17:18.980855 call        28     def __getitem__(self, idx):
13:17:18.981013 line        29         if self.mode == "test":
13:17:18.981100 line        30             text_a, text_b = self.df.iloc[idx, :2].values
New var:....... text_a = '齐齐哈尔市有特大暴雨可能有1998年的洪水那么大'
New var:....... text_b = '网传济南今晚有特大暴雨，可能有1998年那么大的洪水？你造谣良心不痛吗！'
13:17:18.982109 line        31             label_tensor = None
New var:....... label_tensor = None
13:17:18.982318 line        39         word_pieces = ["[CLS]"]
New var:....... word_pieces = ['[CLS]']
13:17:18.982426 line        40         tokens_a = self.tokenizer.tokenize(text_a)
New var:....... token

CPU times: user 5h 6min 33s, sys: 5min 32s, total: 5h 12min 6s
Wall time: 5h 9min 34s


In [ ]:
!ls bert*.csv

bert_1_prec_training_samples.csv
